# Clustering

This notebook will be investigating the proper clustering method based on the results from Feature_Selection notebook. This notebook show some potential that the dimension reduction by feature selection and PCA show some potential that this could have some potential even with visual clustering.
Therefore we will be investigating sophisticated method of clustering and it will improve based on this result.






In [1]:
import os
# Set the environment variable
os.environ['OMP_NUM_THREADS'] = '1'

import pandas as pd
from sklearn.mixture import GaussianMixture
import plotly.express as px
import matplotlib.pyplot as plt
import numpy as np
from sklearn.preprocessing import StandardScaler
import seaborn as sns


import matplotlib.pyplot as plt
import seaborn as sns
import random
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE

# Load the data

In [2]:
# Read CSV files into DataFrames
df_mi_corr = pd.read_csv("../processed_data/lazy_corr_MI_10_FS.csv")
df_mi_corr_50 = pd.read_csv("../processed_data/lazy_corr_MI_50_FS.csv")
df_corr = pd.read_csv("../processed_data/lazy_corr_FS.csv")
df_mi = pd.read_csv("../processed_data/batch_corr_MI_10_FS.csv")
df = pd.read_csv("../processed_data/batch_corr_FS.csv")
df_mi_50= pd.read_csv("../processed_data/batch_corr_MI_50_FS.csv")


df_corr_scaled_mi_batch_50= pd.read_csv("../processed_data/batch_corr_batch_MI_50_FS.csv")

df_corr_scaled_nomiddle= pd.read_csv("../processed_data/batch_corr_MI_nomiddle_50_FS.csv")

df_corr_scaled_mi_nofreq_50= pd.read_csv("../processed_data/batch_corr_MI_nofreq_50_FS.csv")

First we will be investigating df_mi and df_mi_50 that had good visualization result using PCA. Following figures were the results:

Based on the analytics and the nature of the clustering method where we want to find anomalies Gaussian Mixture model will be first thing to be investigated. 

<img src="https://scikit-learn.org/stable/_images/sphx_glr_plot_cluster_comparison_001.png" alt="sphx_glr_plot_cluster_comparison_001" width="1200"/>


## Evaluation Methods
One of the hard thing about the clustering is how to evaluate the clustering. To do so we will leverage the nature of our dataset.

weighted average of average variability of pingtime: This will reveals the how much variability within the cluster. This does not compare each cluster's quality and having more cluster is always better but this doesn't account that either.


In [3]:
def identify_outliers(series):
    Q1 = series.quantile(0.25)
    Q3 = series.quantile(0.75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR
    return ((series < lower_bound) | (series > upper_bound)).sum()

def average_variability_metrics(df_cluster, all_cleaned_df):
    """
    Calculate the average number of outliers and average standard deviation of ping time for each cluster,
    and the weighted averages of these values.

    Parameters:
    df_cluster (DataFrame): The DataFrame containing sensor ID and their respective clusters.
    all_cleaned_df (DataFrame): The DataFrame containing the cleaned data.

    Returns:
    DataFrame: A DataFrame with columns for cluster, average number of outliers, and average std ping time.
    float: The weighted average of the average number of outliers across clusters.
    float: The weighted average of the average standard deviation of ping time across clusters.
    """

    # List to store the results
    results = []

    # Iterate over each cluster
    for target in df_cluster["cluster"].unique():
        # Get the sensor IDs for the current cluster
        cluster_sensors = df_cluster[df_cluster["cluster"] == target]["Sensor ID"].unique()

        # Filter the all_cleaned_df for the current cluster sensors
        all_cleaned_df_target = all_cleaned_df[all_cleaned_df['Sensor ID'].isin(cluster_sensors)]

        # Group by 'Delay (us)' and 'Range (cm)', then calculate the number of outliers in 'Ping Time (us)'
        grouped_outliers = all_cleaned_df_target.groupby(['Delay (us)', 'Range (cm)'])['Ping Time (us)'].apply(identify_outliers).reset_index(name='outliers')
        
        # Calculate the average number of outliers for the current cluster
        avg_count_outliers = grouped_outliers['outliers'].mean()
        max_count_outliers = grouped_outliers['outliers'].max()

        # Group by sensor ID, delay, and range, then calculate the standard deviation of ping time
        grouped_std = all_cleaned_df_target.groupby(['Sensor ID', 'Delay (us)', 'Range (cm)']).agg(
            std_ping_time=('Ping Time (us)', 'std')
        ).reset_index()

        # Calculate the average std ping time for the current cluster
        avg_std_ping_time = grouped_std['std_ping_time'].mean()

        # Append the results to the list
        results.append({'cluster': target, 'max_count_outliers':max_count_outliers, 'avg_count_outliers': avg_count_outliers, 'avg_std_ping_time': avg_std_ping_time, 'count': len(cluster_sensors)})
    
    # Convert the results list to a DataFrame
    results_df = pd.DataFrame(results)
    
    # Calculate the weighted average of the average number of outliers

    results_df['weighted_avg_count_outliers'] =(results_df['max_count_outliers']-results_df['avg_count_outliers']) /results_df['count']
    weighted_avg_count_outliers_score = results_df['weighted_avg_count_outliers'].mean()

    # Calculate the weighted average of the average std ping time
    results_df['weighted_avg_std_ping_time'] = results_df['avg_std_ping_time'] /results_df['count']*(results_df['cluster']+1)
    weighted_avg_std_ping_time_score = results_df['weighted_avg_std_ping_time'].mean()

    return results_df, weighted_avg_count_outliers_score, weighted_avg_std_ping_time_score



Based on the result we will be investigating the when n component is 7 and 11.

### Visual Investigate Clustering performance

In [4]:
def visualize_lineplot_ping_time_with_variability(df, target = []):
    """
    Visualize the effect of range on ping time for each delay separately with variability.

    Parameters:
    df (DataFrame): The DataFrame containing the data.
    """
    # Group by sensor ID, delay, and range, then calculate the mean and standard deviation of ping time
    grouped_df = df.groupby(['Sensor ID', 'Delay (us)', 'Range (cm)']).agg(
        mean_ping_time=('Ping Time (us)', 'mean'),
        std_ping_time=('Ping Time (us)', 'std')
    ).reset_index()

    target_df = grouped_df[grouped_df['Sensor ID'].isin(target)]
    # Get unique delays
    unique_delays = target_df['Delay (us)'].unique()

    for delay in unique_delays:
        subset_df = target_df[target_df['Delay (us)'] == delay]

        fig = px.line(

        )

        # Adding error bars
        for sensor_id in subset_df['Sensor ID'].unique():
            sensor_data = subset_df[subset_df['Sensor ID'] == sensor_id]
            fig.add_trace(
                go.Scatter(
                    x=sensor_data['Range (cm)'],
                    y=sensor_data['mean_ping_time'],
                    mode='lines+markers',
                    name=f'Sensor {sensor_id}',
                    error_y=dict(
                        type='data',
                        array=sensor_data['std_ping_time'],
                        visible=True
                    )
                )
            )

        # Plot reference line
        ranges = np.linspace(subset_df['Range (cm)'].min(), subset_df['Range (cm)'].max(), 100)
        reference_ping_times = 57 * ranges
        fig.add_trace(
            go.Scatter(
                x=ranges,
                y=reference_ping_times,
                mode='lines',
                line=dict(color='red', dash='dash'),
                name='Reference Line'
            )
        )

        fig.update_layout(
            xaxis_title='Range (cm)',
            yaxis_title='Mean Ping Time (us)',
            legend_title='Sensor ID',
            template='plotly_white'
        )

        fig.show()

def visualize_lineplot_ping_time_with_variability_simple(df, target=[]):
    """
    Visualize the effect of range on ping time for each delay separately with variability.

    Parameters:
    df (DataFrame): The DataFrame containing the data.
    target (list): List of target sensor IDs to visualize.
    """
    # Group by sensor ID, delay, and range, then calculate the mean and standard deviation of ping time
    grouped_df = df.groupby(['Sensor ID', 'Delay (us)', 'Range (cm)']).agg(
        mean_ping_time=('Ping Time (us)', 'mean'),
        std_ping_time=('Ping Time (us)', 'std')
    ).reset_index()

    target_df = grouped_df[grouped_df['Sensor ID'].isin(target)]
    # Get unique delays
    unique_delays = target_df['Delay (us)'].unique()

    # Define the number of columns for subplots
    num_columns = 2  # 2 columns for the grid
    num_rows = 3  # 3 rows for the grid

    # Create subplots
    fig = make_subplots(rows=num_rows, cols=num_columns, subplot_titles=[f'Delay: {delay} us' for delay in unique_delays])

    for i, delay in enumerate(unique_delays):
        subset_df = target_df[target_df['Delay (us)'] == delay]

        # Get the row and column position for the subplot
        row = (i // num_columns) + 1
        col = (i % num_columns) + 1

        # Adding error bars
        for sensor_id in subset_df['Sensor ID'].unique():
            sensor_data = subset_df[subset_df['Sensor ID'] == sensor_id]
            fig.add_trace(
                go.Scatter(
                    x=sensor_data['Range (cm)'],
                    y=sensor_data['mean_ping_time'],
                    mode='lines+markers',
                    name=f'Sensor {sensor_id}',
                    error_y=dict(
                        type='data',
                        array=sensor_data['std_ping_time'],
                        visible=True
                    )
                ),
                row=row, col=col
            )

        # Plot reference line
        ranges = np.linspace(subset_df['Range (cm)'].min(), subset_df['Range (cm)'].max(), 100)
        reference_ping_times = 57 * ranges
        fig.add_trace(
            go.Scatter(
                x=ranges,
                y=reference_ping_times,
                mode='lines',
                line=dict(color='red', dash='dash'),
                name='Reference Line'
            ),
            row=row, col=col
        )

    fig.update_layout(
        height=1500,  # Adjust height for the grid layout
        width=1500,  # Adjust width for the grid layout
        showlegend=False,
        title_text="Ping Time vs Range for Different Delays"
    )

    fig.show()

def visualize_cluster(df,cluster = 0, simple = True):
    # Load the dataset
    file_path = '../processed_data/all_data_v4-1-1_cleaned_sensor211.csv'
    all_cleaned_df = pd.read_csv(file_path)
    all_cleaned_df = all_cleaned_df.drop("Unnamed: 0",axis=1)
    
    cluster_sensors = df[df["cluster"]==cluster]["Sensor ID"].unique()
    if simple:
        visualize_lineplot_ping_time_with_variability_simple(all_cleaned_df,cluster_sensors)
    else:
        visualize_lineplot_ping_time_with_variability(all_cleaned_df,cluster_sensors)
    

# K-Means

### Helper codes

In [5]:
# Load the dataset
file_path = '../processed_data/all_data_v4-1-1_cleaned_sensor211.csv'
all_cleaned_df = pd.read_csv(file_path)
all_cleaned_df = all_cleaned_df.drop("Unnamed: 0",axis=1)

In [6]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans
import plotly.express as px
import plotly.graph_objs as go

def tune_and_visualize_kmeans(data, n_clusters_range=range(1, 11), plot_3d=False):
    """
    Perform hyperparameter tuning for KMeans clustering,
    store the results in a DataFrame, visualize the results, and return the best model.
    Optionally, create an interactive 3D plot of the clustering results.

    Parameters:
    - data: pd.DataFrame - The input data for KMeans clustering.
    - n_clusters_range: range - The range of number of clusters to try.
    - plot_3d: bool - Whether to create an interactive 3D plot of the clustering results.

    Returns:
    - best_model: KMeans - The best KMeans model based on the inertia criterion.
    - results_df: pd.DataFrame - The DataFrame containing inertia values for each model.
    """
    
    # Drop the target column if it's present
    if 'target' in data.columns:
        data = data.drop('target', axis=1)

    # Standardize the features
    scaler = StandardScaler()
    features_scaled = scaler.fit_transform(data)

    # Create lists to store the results
    inertia_values = []
    n_clusters_list = []

    # Loop over the range of clusters
    for n_clusters in n_clusters_range:
        kmeans = KMeans(n_clusters=n_clusters, n_init='auto',random_state=42)
        kmeans.fit(features_scaled)
        
        inertia = kmeans.inertia_
        
        inertia_values.append(inertia)
        n_clusters_list.append(n_clusters)

    # Create a DataFrame to store the results
    results_df = pd.DataFrame({
        'n_clusters': n_clusters_list,
        'Inertia': inertia_values
    })

    # Plot the inertia values
    fig = px.line(results_df, x='n_clusters', y='Inertia', 
                  title='Inertia values for different number of clusters',
                  labels={'Inertia': 'Inertia', 'n_clusters': 'Number of Clusters'},
                  markers=True)
    fig.show()

    # Find the best model based on the inertia (elbow method)
    best_index = results_df['Inertia'].idxmin()
    best_n_clusters = results_df.loc[best_index, 'n_clusters']
    best_model = KMeans(n_clusters=best_n_clusters, random_state=42)
    best_model.fit(features_scaled)

    # Optionally, create an interactive 3D plot of the clustering results
    if plot_3d:
        if features_scaled.shape[1] < 3:
            raise ValueError("The dataset must have at least 3 features for a 3D plot.")
        
        # Predict cluster labels
        cluster_labels = best_model.predict(features_scaled)
        data['cluster'] = cluster_labels
        
        # Create 3D scatter plot
        fig_3d = px.scatter_3d(
            data, 
            x=features_scaled[:, 0], 
            y=features_scaled[:, 1], 
            z=features_scaled[:, 2], 
            color='cluster',
            title='KMeans Clustering Results in 3D',
            labels={'x': 'Feature 1', 'y': 'Feature 2', 'z': 'Feature 3'}
        )
        fig_3d.show()

    return best_model, results_df


In [7]:
def train_KMeans(df, n_clusters=5, random_state=42, visualization_method='PCA', plot_3d=False):
    """
    Train a KMeans model on the given dataframe, predict clusters, and visualize the results.

    Parameters:
    df (DataFrame): The DataFrame containing the features to cluster.
    n_clusters (int): The number of clusters for KMeans.
    random_state (int): Random state for reproducibility.
    visualization_method (str): The method for visualization ('PCA' or 'TSNE').
    plot_3d (bool): Whether to generate a 3D plot. If False, a 2D plot will be generated.

    Returns:
    DataFrame: The original DataFrame with an additional column for cluster labels.
    KMeans: The fitted KMeans model.
    """

    # Standardize the features
    df = df.copy()
    sensor_ids = df.index if 'Sensor ID' not in df.columns else df['Sensor ID']
    scaler = StandardScaler()
    features_scaled = scaler.fit_transform(df.drop(columns=['Sensor ID']))

    # Fit a KMeans model
    kmeans = KMeans(n_clusters=n_clusters, random_state=random_state)
    kmeans.fit(features_scaled)

    # Predict cluster labels
    cluster_labels = kmeans.predict(features_scaled)
    df['cluster'] = cluster_labels

    print("============ Distribution of Sensors in each Cluster ============")
    print(df.groupby(["cluster"])["Sensor ID"].count())

    # Evaluate the model using inertia
    inertia = kmeans.inertia_
    print(f"Inertia: {inertia}")

    # Visualize the clustering results using PCA or t-SNE
    if visualization_method.upper() == 'PCA':
        n_components = 3 if plot_3d else 2
        pca = PCA(n_components=n_components)
        components = pca.fit_transform(features_scaled)
        title = '3D Visualization using PCA' if plot_3d else '2D Visualization using PCA'
    elif visualization_method.upper() == 'TSNE':
        n_components = 3 if plot_3d else 2
        tsne = TSNE(n_components=n_components, random_state=random_state)
        components = tsne.fit_transform(features_scaled)
        title = '3D Visualization using t-SNE' if plot_3d else '2D Visualization using t-SNE'
    else:
        raise ValueError("visualization_method should be either 'PCA' or 'TSNE'.")

    # Create a DataFrame for the components
    components_df = pd.DataFrame(components, columns=[f'Component {i+1}' for i in range(n_components)])
    components_df['cluster'] = cluster_labels
    components_df['Sensor ID'] = sensor_ids

    # Plot the results
    if plot_3d:
        fig = px.scatter_3d(
            components_df, 
            x='Component 1', 
            y='Component 2', 
            z='Component 3', 
            color='cluster', 
            title=title,
            hover_name='Sensor ID'  # Display Sensor ID on hover
        )
    else:
        fig = px.scatter(
            components_df, 
            x='Component 1', 
            y='Component 2', 
            color='cluster', 
            title=title,
            hover_name='Sensor ID'  # Display Sensor ID on hover
        )
    
    fig.show()

    return df, kmeans

In [8]:
def search_kmeans_weighted_avg(df,data, n_components_range=range(2, 20)):
    for i in n_components_range:
        # Standardize the features
        scaler = StandardScaler()
        features_scaled = scaler.fit_transform(df)

        # Fit a KMeans model
        kmeans = KMeans(n_clusters=i, n_init='auto', random_state=42)
        kmeans.fit(features_scaled)


        # Predict cluster labels
        cluster_labels = kmeans.predict(features_scaled)
        df['cluster'] = cluster_labels
        
        results_df, weighted_avg_outliers_score, weighted_avg_std_ping_time_score = average_variability_metrics(df,data)
        #print(results_df)
        #print(f"============== {i} component(s) ================")
        print(f"Weighted average of variability score when {i} component(s): ", weighted_avg_std_ping_time_score,f" Outlier score when {i} component(s): ", weighted_avg_outliers_score)


### Investigate each feature sets

#### feature set with no freq and feature selection

In [9]:
best_kmeans_model, tuning_results = tune_and_visualize_kmeans(df_corr_scaled_mi_nofreq_50, n_clusters_range=range(1, 30), plot_3d=False)
print(best_kmeans_model)

KMeans(n_clusters=29, random_state=42)


c:\Anaconda\envs\datascience\lib\site-packages\sklearn\cluster\_kmeans.py:1412: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



In [10]:
search_kmeans_weighted_avg(df_corr_scaled_mi_nofreq_50,all_cleaned_df)

Weighted average of variability score when 2 component(s):  1.961180171182679  Outlier score when 2 component(s):  4.041236988622609
Weighted average of variability score when 3 component(s):  12.78628599913489  Outlier score when 3 component(s):  7.665733541786942
Weighted average of variability score when 4 component(s):  4.110853376728823  Outlier score when 4 component(s):  7.006651434984769
Weighted average of variability score when 5 component(s):  16.31811030636407  Outlier score when 5 component(s):  5.941326957285916
Weighted average of variability score when 6 component(s):  55.230723081769064  Outlier score when 6 component(s):  10.196667042917042
Weighted average of variability score when 7 component(s):  41.64019943447979  Outlier score when 7 component(s):  9.179378495950823
Weighted average of variability score when 8 component(s):  18.726695135403716  Outlier score when 8 component(s):  6.458075985317365
Weighted average of variability score when 9 component(s):  39.366

In [11]:
df_nofreq, kmeans = train_KMeans(df_corr_scaled_mi_nofreq_50, n_clusters=8, random_state=42, visualization_method='PCA', plot_3d=True)

============ Distribution of Sensors in each Cluster ============
cluster
0    33
1    29
2    15
3     7
4    44
5    78
6     3
7     1
Name: Sensor ID, dtype: int64
Inertia: 7837.266211002821


c:\Anaconda\envs\datascience\lib\site-packages\sklearn\cluster\_kmeans.py:1412: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



In [12]:
results_df, ping_time_clustering_score,weighted_avg_std_ping_time_score = average_variability_metrics(df_nofreq,all_cleaned_df)

print(ping_time_clustering_score)
results_df

8.92715581991444


cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        0                 279           54.822222          17.319243     33   
1        2                 235           41.088889          97.857459     15   
2        5                 548          110.133333         128.697850     78   
3        4                 198           68.488889          39.313025     44   
4        1                 202           54.888889         103.009516     29   
5        6                  59            5.733333         605.100547      3   
6        7                  19            4.644444          13.420619      1   
7        3                  46            4.311111         853.812177      7   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     6.793266                    0.524826  
1                    12.927407                   19.571492  
2                     5.613675                    9.899835  
3                     2.943434                    4.467389  
4                     5.072797                    7.104105  
5                    17.755556                 1411.901277  
6                    14.355556                  107.364954  
7                     5.955556                  487.892673

In [13]:
visualize_cluster(df_nofreq,0)

In [14]:
visualize_cluster(df_nofreq,1)

In [15]:
visualize_cluster(df_nofreq,2)

In [16]:
visualize_cluster(df_nofreq,3)

In [17]:
visualize_cluster(df_nofreq,4)

In [18]:
visualize_cluster(df_nofreq,5)

In [19]:
visualize_cluster(df_nofreq,6)

In [20]:
visualize_cluster(df_nofreq,7)

#### feature set with minimal feature selection

In [21]:
best_kmeans_model, tuning_results = tune_and_visualize_kmeans(df_mi, n_clusters_range=range(1, 30), plot_3d=False)
print(best_kmeans_model)

KMeans(n_clusters=29, random_state=42)


c:\Anaconda\envs\datascience\lib\site-packages\sklearn\cluster\_kmeans.py:1412: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



In [22]:
search_kmeans_weighted_avg(df_mi,all_cleaned_df)

Weighted average of variability score when 2 component(s):  1.8510195060217134  Outlier score when 2 component(s):  3.8392087096676093
Weighted average of variability score when 3 component(s):  12.901329320357567  Outlier score when 3 component(s):  4.182465595631151
Weighted average of variability score when 4 component(s):  38.06075550726847  Outlier score when 4 component(s):  7.7500716937600025
Weighted average of variability score when 5 component(s):  46.6937356114414  Outlier score when 5 component(s):  10.098927687248272
Weighted average of variability score when 6 component(s):  45.91220709578943  Outlier score when 6 component(s):  10.547383699007126
Weighted average of variability score when 7 component(s):  36.3980202728923  Outlier score when 7 component(s):  9.931947056527639
Weighted average of variability score when 8 component(s):  398.8213703737549  Outlier score when 8 component(s):  9.591700788934341
Weighted average of variability score when 9 component(s):  331.8

In [23]:
df_mi_cluster, kmeans = train_KMeans(df_mi, n_clusters=7, random_state=42, visualization_method='PCA', plot_3d=True)

============ Distribution of Sensors in each Cluster ============
cluster
0    94
1    51
2    26
3     1
4    36
5     1
6     1
Name: Sensor ID, dtype: int64
Inertia: 896.6900252740401


c:\Anaconda\envs\datascience\lib\site-packages\sklearn\cluster\_kmeans.py:1412: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



In [24]:
results_df, ping_time_clustering_score,weighted_avg_std_ping_time_score = average_variability_metrics(df_nofreq,all_cleaned_df)

print(ping_time_clustering_score)
results_df

8.92715581991444


cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        0                 279           54.822222          17.319243     33   
1        2                 235           41.088889          97.857459     15   
2        5                 548          110.133333         128.697850     78   
3        4                 198           68.488889          39.313025     44   
4        1                 202           54.888889         103.009516     29   
5        6                  59            5.733333         605.100547      3   
6        7                  19            4.644444          13.420619      1   
7        3                  46            4.311111         853.812177      7   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     6.793266                    0.524826  
1                    12.927407                   19.571492  
2                     5.613675                    9.899835  
3                     2.943434                    4.467389  
4                     5.072797                    7.104105  
5                    17.755556                 1411.901277  
6                    14.355556                  107.364954  
7                     5.955556                  487.892673

##### Cluster 0: Over measurement

In [25]:
visualize_cluster(df_mi_cluster,0)

##### Cluster 1: Struggle on delay 8000us 

In [26]:
visualize_cluster(df_mi_cluster,1)

##### Cluster 2: struggles on delay 16800

In [27]:
visualize_cluster(df_mi_cluster,2)

In [28]:
visualize_cluster(df_mi_cluster,3)

##### Cluster 4: over measurements 

In [29]:
visualize_cluster(df_mi_cluster,4)

In [30]:
visualize_cluster(df_mi_cluster,5)

In [27]:
visualize_cluster(df_mi_cluster,6)

#### feature set batch mutrual information feature selection

In [31]:
best_kmeans_model, tuning_results = tune_and_visualize_kmeans(df_corr_scaled_mi_batch_50, n_clusters_range=range(1, 30), plot_3d=False)
print(best_kmeans_model)

KMeans(n_clusters=29, random_state=42)


c:\Anaconda\envs\datascience\lib\site-packages\sklearn\cluster\_kmeans.py:1412: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



In [32]:
search_kmeans_weighted_avg(df_corr_scaled_mi_batch_50,all_cleaned_df)

Weighted average of variability score when 2 component(s):  1.7560393061789186  Outlier score when 2 component(s):  3.953178323070796
Weighted average of variability score when 3 component(s):  5.1818834853076075  Outlier score when 3 component(s):  7.925871878022416
Weighted average of variability score when 4 component(s):  6.3212419542246465  Outlier score when 4 component(s):  7.964926768397207
Weighted average of variability score when 5 component(s):  28.342636285565323  Outlier score when 5 component(s):  6.315813821484319
Weighted average of variability score when 6 component(s):  28.61854570988403  Outlier score when 6 component(s):  7.625300736559801
Weighted average of variability score when 7 component(s):  50.385425776225006  Outlier score when 7 component(s):  9.689914227516027
Weighted average of variability score when 8 component(s):  19.104381518670795  Outlier score when 8 component(s):  6.295355520635999
Weighted average of variability score when 9 component(s):  43.

In [55]:
df_batch_mi, kmeans = train_KMeans(df_corr_scaled_mi_batch_50, n_clusters=17, random_state=42, visualization_method='TSNE', plot_3d=True)

c:\Anaconda\envs\datascience\lib\site-packages\sklearn\cluster\_kmeans.py:1412: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



============ Distribution of Sensors in each Cluster ============
cluster
0      8
1     35
2     18
3     36
4      1
5     21
6     10
7      7
8      1
9     13
10     1
11    24
12     1
13     1
14     4
15     2
16    27
Name: Sensor ID, dtype: int64
Inertia: 6530.968027594317


In [34]:
results_df, ping_time_clustering_score,weighted_avg_std_ping_time_score = average_variability_metrics(df_corr_scaled_mi_batch_50,all_cleaned_df)

print(ping_time_clustering_score)
results_df

10.906182065956719


cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0         5                  82            7.222222          14.708272      7   
1        12                 150           33.622222          36.203974     10   
2         2                 102           15.933333          61.008699     21   
3         0                 171           28.866667          48.811758     14   
4         8                 101           11.555556         114.375306      9   
5        11                  23            5.400000          26.583564      1   
6        17                 114           18.800000          50.549992     12   
7         7                 175           20.266667          97.929151     27   
8         6                 203           63.488889          18.279877     21   
9        10                  26            2.400000         717.283417      2   
10        1                  81           15.488889          67.406828     18   
11       18                  96           15.333333          67.607479      3   
12        3                 145           14.533333          67.674192     16   
13        4                 197           39.622222          98.963125     29   
14       16                  19            4.644444          13.420619      1   
15       13                  46            4.311111         853.812177      7   
16       15                  22            2.622222         380.734807      1   
17        9                  88            9.311111         427.692201     10   
18       14                  23            3.666667          29.022530      1   

    weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     10.682540                   12.607090  
1                     11.637778                   47.065166  
2                      4.098413                    8.715528  
3                     10.152381                    3.486554  
4                      9.938272                  114.375306  
5                     17.600000                  319.002768  
6                      7.933333                   75.824989  
7                      5.730864                   29.016045  
8                      6.643386                    6.093292  
9                     11.800000                 3945.058796  
10                     3.639506                    7.489648  
11                    26.888889                  428.180700  
12                     8.154167                   16.918548  
13                     5.426820                   17.062608  
14                    14.355556                  228.150527  
15                     5.955556                 1707.624355  
16                    19.377778                 6091.756908  
17                     7.868889                  427.692201  
18                    19.333333                  435.337948

##### Cluster 0: over measurement

In [35]:
visualize_cluster(df_batch_mi,0)

##### Cluster 1: over measurement at 28 it seems to go back to reference line


In [36]:
visualize_cluster(df_batch_mi,1)

In [37]:
visualize_cluster(df_batch_mi,2)

In [38]:
visualize_cluster(df_batch_mi,3)

##### Cluster 6: under measurement seems like outliers

In [47]:
visualize_cluster(df_batch_mi,6)

##### Cluster 7: when delay 16800 there are off going at 13cm

In [48]:
visualize_cluster(df_batch_mi,7)

In [51]:
visualize_cluster(df_batch_mi,9)

In [54]:
visualize_cluster(df_batch_mi,11)

##### Cluster 14: when delay is at 8000 off going at 53 

In [58]:
visualize_cluster(df_batch_mi,14)

In [60]:
visualize_cluster(df_batch_mi,16)

## Visualize based on cluster

In [45]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def visualize_lineplot_ping_time_with_variability_by_cluster(df, cluster_sensors, delay=None):
    """
    Visualize the effect of range on ping time for each cluster with variability, optionally filtering by delay.

    Parameters:
    df (DataFrame): The DataFrame containing the data.
    cluster_sensors (dict): Dictionary where keys are cluster labels and values are lists of sensor IDs in each cluster.
    delay (int, optional): If specified, only data for this delay will be plotted. Otherwise, all delays are plotted.
    """
    # Group by sensor ID, range, and delay, then calculate the mean and standard deviation of ping time
    grouped_df = df.groupby(['Sensor ID', 'Range (cm)', 'Delay (us)']).agg(
        mean_ping_time=('Ping Time (us)', 'mean'),
        std_ping_time=('Ping Time (us)', 'std')
    ).reset_index()

    # Filter by the specified delay if provided
    if delay is not None:
        grouped_df = grouped_df[grouped_df['Delay (us)'] == delay]

    # Define the number of columns for subplots
    num_clusters = len(cluster_sensors)
    num_columns = 2  # Number of columns for the grid
    num_rows = (num_clusters + num_columns - 1) // num_columns  # Calculate rows based on the number of clusters

    # Create subplots
    fig = make_subplots(rows=num_rows, cols=num_columns, subplot_titles=[f'Cluster {cluster}' for cluster in cluster_sensors.keys()])

    for i, (cluster, sensors) in enumerate(cluster_sensors.items()):
        cluster_df = grouped_df[grouped_df['Sensor ID'].isin(sensors)]

        # Get the row and column position for the subplot
        row = (i // num_columns) + 1
        col = (i % num_columns) + 1

        # Adding error bars
        for sensor_id in sensors:
            sensor_data = cluster_df[cluster_df['Sensor ID'] == sensor_id]
            fig.add_trace(
                go.Scatter(
                    x=sensor_data['Range (cm)'],
                    y=sensor_data['mean_ping_time'],
                    mode='lines+markers',
                    name=f'Sensor {sensor_id}',
                    error_y=dict(
                        type='data',
                        array=sensor_data['std_ping_time'],
                        visible=True
                    )
                ),
                row=row, col=col
            )

        # Plot reference line
        ranges = np.linspace(cluster_df['Range (cm)'].min(), cluster_df['Range (cm)'].max(), 100)
        reference_ping_times = 57 * ranges
        fig.add_trace(
            go.Scatter(
                x=ranges,
                y=reference_ping_times,
                mode='lines',
                line=dict(color='red', dash='dash'),
                name='Reference Line'
            ),
            row=row, col=col
        )

    fig.update_layout(
        height=3000,  # Adjust height for the grid layout
        width=1500,  # Adjust width for the grid layout
        showlegend=False,
        title_text=f"Ping Time vs Range for Different Clusters {delay}us"
    )

    fig.show()

def visualize_cluster_delay(df, delay_pos=4):
    # Load the dataset
    file_path = '../processed_data/all_data_v4-1-1_cleaned_sensor211.csv'
    all_cleaned_df = pd.read_csv(file_path)
    all_cleaned_df = all_cleaned_df.drop("Unnamed: 0", axis=1)
    
    # Dictionary to store sensors grouped by cluster
    cluster_sensors = df.groupby("cluster")["Sensor ID"].apply(list).to_dict()

    delays = [3000,6000,8000,10000,16800]

    visualize_lineplot_ping_time_with_variability_by_cluster(all_cleaned_df, cluster_sensors, delays[delay_pos])



In [47]:
visualize_cluster_delay(df_batch_mi,delay_pos=0)

In [46]:
visualize_cluster_delay(df_batch_mi,delay_pos=1)

In [48]:
visualize_cluster_delay(df_batch_mi,delay_pos=2)

In [50]:
visualize_cluster_delay(df_batch_mi,delay_pos=4)

## Side-by-Side Comparison of Clusters Across All Delays

In [3]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def visualize_lineplot_ping_time_with_variability_side_by_side(df, cluster_sensors, delays):
    """
    Visualize the effect of range on ping time for selected clusters and delays side-by-side with variability.

    Parameters:
    df (DataFrame): The DataFrame containing the data.
    cluster_sensors (dict): Dictionary where keys are cluster labels and values are lists of sensor IDs in each cluster.
    delays (list): List of delays to compare across clusters.
    """
    # Group by sensor ID, range, and delay, then calculate the mean and standard deviation of ping time
    grouped_df = df.groupby(['Sensor ID', 'Range (cm)', 'Delay (us)']).agg(
        mean_ping_time=('Ping Time (us)', 'mean'),
        std_ping_time=('Ping Time (us)', 'std')
    ).reset_index()

    # Determine number of rows and columns for subplots
    num_clusters = len(cluster_sensors)
    num_delays = len(delays)
    
    num_columns = num_clusters
    num_rows = num_delays
    
    # Create subplots
    fig = make_subplots(
        rows=num_rows, 
        cols=num_columns, 
        subplot_titles=[f'Cluster {cluster} - Delay {delay} us' for delay in delays for cluster in cluster_sensors.keys()]
    )

    for i, cluster in enumerate(cluster_sensors.keys()):
        sensors = cluster_sensors[cluster]
        cluster_df = grouped_df[grouped_df['Sensor ID'].isin(sensors)]
        
        for j, delay in enumerate(delays):
            delay_df = cluster_df[cluster_df['Delay (us)'] == delay]

            # Get the row and column position for the subplot
            row = j + 1
            col = i + 1

            # Adding error bars
            for sensor_id in sensors:
                sensor_data = delay_df[delay_df['Sensor ID'] == sensor_id]
                fig.add_trace(
                    go.Scatter(
                        x=sensor_data['Range (cm)'],
                        y=sensor_data['mean_ping_time'],
                        mode='lines+markers',
                        name=f'Sensor {sensor_id} (Delay {delay} us)',
                        error_y=dict(
                            type='data',
                            array=sensor_data['std_ping_time'],
                            visible=True
                        )
                    ),
                    row=row, col=col
                )

            # Plot reference line
            ranges = np.linspace(delay_df['Range (cm)'].min(), delay_df['Range (cm)'].max(), 100)
            reference_ping_times = 57 * ranges
            fig.add_trace(
                go.Scatter(
                    x=ranges,
                    y=reference_ping_times,
                    mode='lines',
                    line=dict(color='red', dash='dash'),
                    name='Reference Line'
                ),
                row=row, col=col
            )

    fig.update_layout(
        height=500 * num_rows,  # Adjust height based on the number of delays
        width=800 * num_columns,  # Adjust width based on the number of clusters
        showlegend=False,
        title_text="Side-by-Side Comparison of Clusters Across All Delays"
    )

    fig.show()

def visualize_cluster_delay_side_by_side(df, clusters_to_compare, delays=[3000, 6000, 8000, 10000, 16800]):
    """
    Compare multiple clusters across all specified delays side by side.

    Parameters:
    df (DataFrame): The DataFrame containing the data, including clustering information.
    clusters_to_compare (list): List of cluster labels to compare side-by-side.
    delays (list): List of delays to compare.
    """
    # Load the dataset
    file_path = '../processed_data/all_data_v4-1-1_cleaned_sensor211.csv'
    all_cleaned_df = pd.read_csv(file_path)
    all_cleaned_df = all_cleaned_df.drop("Unnamed: 0",axis=1)

    # Dictionary to store sensors grouped by cluster
    cluster_sensors = {cluster: df[df["cluster"] == cluster]["Sensor ID"].unique() for cluster in clusters_to_compare}

    # Visualize side-by-side comparisons for the selected clusters and delays
    visualize_lineplot_ping_time_with_variability_side_by_side(all_cleaned_df, cluster_sensors, delays)


In [53]:
# Assuming df is your dataset containing the clustering information
visualize_cluster_delay_side_by_side(df_batch_mi, clusters_to_compare=[4, 6])


In [98]:
# Assuming df is your dataset containing the clustering information
visualize_cluster_delay_side_by_side(df_batch_mi, clusters_to_compare=[5, 7])


In [99]:
# Assuming df is your dataset containing the clustering information
visualize_cluster_delay_side_by_side(df_batch_mi, clusters_to_compare=[6, 11])


In [54]:
# Assuming df is your dataset containing the clustering information
visualize_cluster_delay_side_by_side(df_batch_mi, clusters_to_compare=[6, 11])


In [100]:
# Assuming df is your dataset containing the clustering information
visualize_cluster_delay_side_by_side(df_batch_mi, clusters_to_compare=[12, 13])


In [5]:
# Assuming df is your dataset containing the clustering information
visualize_cluster_delay_side_by_side(df_batch_mi, clusters_to_compare=[2,3,5,11])


NameError: name 'df_batch_mi' is not defined